In [3]:
import panel as pn


pn.extension()

In [41]:
#this could work if i could render an image using bokeh.plotting.figure

from random import random

from bokeh.models import ColumnDataSource, CustomJS
from bokeh.plotting import figure, show

x = [random() for x in range(500)]
y = [random() for y in range(500)]
color = ["navy"] * len(x)

s = ColumnDataSource(data=dict(x=x, y=y, color=color))
p = figure(width=400, height=400, tools=["box_select","hover"], title="Select Here")
p.circle('x', 'y', color='color', size=8, source=s, alpha=0.4,
         selection_color="firebrick")

#s2 = ColumnDataSource(data=dict(x=[0, 1], ym=[0.5, 0.5]))
#p.line(x='x', y='ym', color="orange", line_width=5, alpha=0.6, source=s2)

#if (inds.length > 0) {
  #      const ym = inds.reduce((a, b) => a + s.data.y[b], 0) / inds.length
  #      s2.data = { x: s2.data.x, ym: [ym, ym] }

s.selected.js_on_change('indices', CustomJS(args=dict(s=s), code="""
    const inds = s.selected.indices
    
    }
"""))


pn.panel(p)

Bokeh(figure)

In [42]:
s.selected.indices

[47]

In [39]:
x[331],y[331]

(0.5990908658402143, 0.2841078940181446)

In [3]:
import numpy as np
from pycromanager import Core
import xarray as xr
import hvplot.xarray
import holoviews as hv

In [4]:
core=Core()

In [27]:
core.wait_for_system()
core.snap_image()
tagged_image = core.get_tagged_image()

height = tagged_image.tags['Height']
width = tagged_image.tags['Width']
pixels = np.reshape(tagged_image.pix,
                newshape=[height, width, tagged_image.pix.shape[0]//(height*width)])


x=list(range(pixels.shape[0]))
y=list(range(pixels.shape[1]))
chan=list(range(pixels.shape[2]))

coords={'x':x,
    'y':y,
    'chan':chan}

pix_array=xr.DataArray(pixels,coords=coords)


s = ColumnDataSource(data=dict(pix_r=pix_array))


pix_array.hvplot.rgb(x='y',y='x',bands='chan',data_aspect=1,flip_yaxis=True,tools=['box_select'])



In [28]:
pix_im

:RGB   [y,x]   (R,G,B)

In [82]:
from __future__ import annotations

import numpy as np

from bokeh import events
from bokeh.io import curdoc, show
from bokeh.layouts import column, row
from bokeh.models import Button, CustomJS, Div, TextInput
from bokeh.plotting import figure


def display_event(div: Div, attributes: list[str] = []) -> CustomJS:
    """
    Function to build a suitable CustomJS to display the current event
    in the div model.
    """
    style = 'float: left; clear: left; font-size: 13px'
    return CustomJS(args=dict(div=div), code=f"""
        const attrs = {attributes};
        const args = [];
        for (let i = 0; i < attrs.length; i++) {{
            const val = JSON.stringify(cb_obj[attrs[i]], function(key, val) {{
                return val.toFixed ? Number(val.toFixed(2)) : val;
            }})
            args.push(attrs[i] + '=' + val)
        }}
        const line = "<span style={style!r}><b>" + cb_obj.event_name + "</b>(" + args.join(", ") + ")</span>\\n";
        const text = div.text.concat(line);
        const lines = text.split("\\n")
        if (lines.length > 35)
            lines.shift();
        div.text = lines.join("\\n");
    """)

# Follows the color_scatter gallery example

N = 4000
x = np.random.random(size=N) * 100
y = np.random.random(size=N) * 100
radii = np.random.random(size=N) * 1.5
colors = np.array([(r, g, 150) for r, g in zip(50+2*x, 30+2*y)], dtype="uint8")

p = figure(tools="pan,wheel_zoom,reset,tap,box_select,box_zoom,undo,redo")

p.scatter(x, y, radius=radii,
          fill_color=colors, fill_alpha=0.6,
          line_color=None)

# Add a div to display events and a button to trigger button click events

div = Div(width=1000)
#button = Button(label="Button", button_type="success", width=300)
#text_input = TextInput(placeholder="Input a value and press Enter ...", width=300)
layout = column(row(p, div))#,button, text_input)

# Register event callbacks

# Button events
#button.js_on_event(events.ButtonClick, display_event(div))

# TextInput events
#text_input.js_on_event(events.ValueSubmit, display_event(div, ["value"]))

# LOD events
#p.js_on_event(events.LODStart, display_event(div))
#p.js_on_event(events.LODEnd, display_event(div))

# Point events
point_attributes = ['x','y','sx','sy']
p.js_on_event(events.Tap,       display_event(div, attributes=point_attributes))
p.js_on_event(events.DoubleTap, display_event(div, attributes=point_attributes))
p.js_on_event(events.Press,     display_event(div, attributes=point_attributes))
p.js_on_event(events.PressUp,   display_event(div, attributes=point_attributes))

# Mouse wheel event
#p.js_on_event(events.MouseWheel, display_event(div,attributes=[*point_attributes, 'delta']))

# Mouse move, enter and leave
# p.js_on_event(events.MouseMove,  display_event(div, attributes=point_attributes))
#p.js_on_event(events.MouseEnter, display_event(div, attributes=point_attributes))
#p.js_on_event(events.MouseLeave, display_event(div, attributes=point_attributes))

# Pan events
#pan_attributes = [*point_attributes, 'delta_x', 'delta_y']
#p.js_on_event(events.Pan,      display_event(div, attributes=pan_attributes))
#p.js_on_event(events.PanStart, display_event(div, attributes=point_attributes))
#p.js_on_event(events.PanEnd,   display_event(div, attributes=point_attributes))

# Pinch events
#pinch_attributes = [*point_attributes, 'scale']
#p.js_on_event(events.Pinch,      display_event(div, attributes=pinch_attributes))
#p.js_on_event(events.PinchStart, display_event(div, attributes=point_attributes))
#p.js_on_event(events.PinchEnd,   display_event(div, attributes=point_attributes))

# Ranges Update events
p.js_on_event(events.RangesUpdate, display_event(div, attributes=['x0','x1','y0','y1']))

# Selection events
p.js_on_event(events.SelectionGeometry, display_event(div, attributes=['geometry', 'final']))

curdoc().on_event(events.DocumentReady, display_event(div))
pn.panel(layout)

Bokeh(Column)

In [83]:
div.text

'<span style=\'float: left; clear: left; font-size: 13px\'><b>tap</b>(x=109.64, y=87.65, sx=585.75, sy=99.73)</span>\n<span style=\'float: left; clear: left; font-size: 13px\'><b>selectiongeometry</b>(geometry={"type":"rect","sx0":299.66,"sx1":358.48,"sy0":115.64,"sy1":191.55,"x0":49.58,"y0":69.59,"x1":61.93,"y1":84.52}, final=true)</span>\n'

[]